# Setup

In [1]:
! pip install --quiet transformers shap sentencepiece datasets --upgrade

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 19.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.9/547.9 kB 33.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 36.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.3/519.3 kB 40.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 31.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 51.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 48.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 17.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 23.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 16.9 MB/s eta 0:00:00


In [2]:
import transformers
import shap
import torch
import datasets

import numpy as np
import scipy as sp

from transformers import AutoTokenizer, AutoModelForCausalLM

# 1 - mGPT Model

In [4]:
model_path = 'ai-forever/mGPT'
tokenizer = AutoTokenizer.from_pretrained(model_path)
model = AutoModelForCausalLM.from_pretrained(model_path).cuda()

In [5]:
model.config.is_decoder=True

gen_dict = dict(
    do_sample=True,
    max_length=20,
    temperature=0.7,
    top_k=50,
    no_repeat_ngram_size=2,
    max_new_tokens=25
)
model.config.task_specific_params = dict()
model.config.task_specific_params["text-generation"] = gen_dict

In [6]:
s = ['Cats are better than dogs because']

In [7]:
shap_model = shap.models.TeacherForcing(model, tokenizer)
masker = shap.maskers.Text(tokenizer, mask_token="...", collapse_mask_token=True)
explainer = shap.Explainer(shap_model, tokenizer)
shap_values = explainer(s)

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Partition explainer: 2it [00:10, 10.24s/it]               


In [8]:
shap.plots.text(shap_values)

#  2 - Bloom Model

In [9]:
from transformers import BloomForCausalLM
from transformers import BloomTokenizerFast

In [10]:
tokenizer = BloomTokenizerFast.from_pretrained("bigscience/bloom-560m")
model = BloomForCausalLM.from_pretrained("bigscience/bloom-560m")

In [11]:
s = ['Cats are better than dogs because']

In [12]:
model.config.is_decoder=True

gen_dict = dict(
    do_sample=True,
    max_length=20,
    temperature=0.7,
    top_k=50,
    no_repeat_ngram_size=2,
    max_new_tokens=25
)
model.config.task_specific_params = dict()
model.config.task_specific_params["text-generation"] = gen_dict

In [13]:
shap_model = shap.models.TeacherForcing(model, tokenizer)
masker = shap.maskers.Text(tokenizer, mask_token="...", collapse_mask_token=True)
explainer = shap.Explainer(shap_model, tokenizer)
shap_values = explainer(s)

`position_ids` have no functionality in BLOOM and will be removed in v5.0.0. You can safely ignore passing `position_ids`.


  0%|          | 0/42 [00:00<?, ?it/s]

Partition explainer: 2it [00:35, 35.68s/it]               


In [14]:
shap.plots.text(shap_values)

# 3 - Pythia Model

In [15]:
from transformers import GPTNeoXForCausalLM, AutoTokenizer

In [16]:
tokenizer = AutoTokenizer.from_pretrained("EleutherAI/pythia-410m-v0")
model = GPTNeoXForCausalLM.from_pretrained("EleutherAI/pythia-410m-v0").cuda()

In [17]:
model.config.is_decoder=True

gen_dict = dict(
    do_sample=True,
    max_length=20,
    temperature=0.7,
    top_k=50,
    no_repeat_ngram_size=2,
    max_new_tokens=25
)
model.config.task_specific_params = dict()
model.config.task_specific_params["text-generation"] = gen_dict

In [18]:
s = ['Cats are better than dogs because']

In [19]:
shap_model = shap.models.TeacherForcing(model, tokenizer)
masker = shap.maskers.Text(tokenizer, mask_token="...", collapse_mask_token=True)
explainer = shap.Explainer(shap_model, tokenizer)
shap_values = explainer(s)

Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.


In [20]:
shap.plots.text(shap_values)